In [1]:
import time
import pandas as pd
import json
from datetime import datetime
from datetime import timezone


import numpy as np
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
from matplotlib.ticker import ScalarFormatter
from matplotlib.colors import ListedColormap

import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Code

In [2]:
def read_json_from_ros2bag(json_file, print_ = True):
    list_of_length = []
    with open(json_file, 'r') as file:
        json_content = json.load(file)
    if print_:
        print('Read: ',json_file)
    for key, value in json_content.items():
        if print_:
            print(f"{key} range: {len(value)}")
        list_of_length.append(len(value))
    cut_data = {key: value[:min(list_of_length)] for key, value in json_content.items()}
    cut_df = pd.DataFrame(cut_data)
    return cut_df
def read_and_normalize_json_from_ros2bag(json_file, print_=True):
    list_of_length = []
    with open(json_file, 'r') as f:
        data = json.load(f)
    if print_:
        print('Read: ',json_file)
    for key, value in data.items():
        if print_:
            print(f"{key} range: {len(value)}")
        list_of_length.append(len(value))
    # Normalize the data into a DataFrame
    df = pd.json_normalize(data)
    return df

def process_sensor_data(input_df, sensor_key, output_column, window_slide=1, shift=0):
    sensor_val = []
    sensor_ts = []
    sensor_df = []

    for i in range(len(input_df[sensor_key][0])):
        sensor_val.append(input_df[sensor_key][0][i]['val'])
        sensor_ts.append(input_df[sensor_key][0][i]['ts'])

    sensor_df = pd.DataFrame(sensor_val, columns=output_column)
    sensor_df = sensor_df.shift(shift)
    sensor_df = sensor_df.rolling(window=window_slide).mean()
    sensor_df['ts'] = sensor_ts

    return sensor_df

In [3]:
df        = read_and_normalize_json_from_ros2bag('lower_limb_exo/stair/subject2_OAIC_S1_Stair_1.json', print_=False)

shift = 0

window_slide = 100
stair_joint_cmd_df = process_sensor_data(df, 'JointCmd',        ['RH','RK','RA','LH','LK','LA'], window_slide, shift)
stair_joint_fb_df  = process_sensor_data(df, 'JointAngles',        ['RH','RK','RA','LH','LK','LA'], window_slide, shift)
stair_foot_force_df = process_sensor_data(df, 'FootPressure',        ['Rheel','Rtoe','Lheel','Ltoe'], window_slide, shift)

In [4]:
df        = read_and_normalize_json_from_ros2bag('lower_limb_exo/symmetrical_walk/subject_1/subject1_OAIC_S38_4.json', print_=False)

shift = 0

window_slide = 1
sym_joint_cmd_df = process_sensor_data(df, 'GaitStep',        ['RH','RK','RA','LH','LK','LA'], window_slide, shift)
sym_joint_fb_df  = process_sensor_data(df, 'JointAngles',        ['RH','RK','RA','LH','LK','LA'], window_slide, shift)
sym_foot_force_df = process_sensor_data(df, 'FootPressure',        ['Rheel','Rtoe','Lheel','Ltoe'], window_slide, shift)

## Plot Sample

In [5]:
# import matplotlib.pyplot as plt
# plt.rcParams['font.size'] = 13
# plt.rcParams['xtick.labelsize'] = 13 
# plt.rcParams['ytick.labelsize'] = 13 
# class ScalarFormatterClass(ScalarFormatter):
#    def _set_format(self):
#       self.format = "%1.2f"

# row_num = 4
# col_num = 2
# fig, ax = plt.subplots(row_num, col_num, sharey=False, gridspec_kw={ 'wspace':0.1, 'hspace':0.2}, figsize=(25, 10))

# time_period = 17
# # ===========================================
# #                 
# # ===========================================

# ax[0,1].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['RH']), label='qd [RH]')
# ax[0,1].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['RH']), label='q [RH]')
# ax[0,1].set_ylabel('Joint angle (deg)')
# ax[0,1].legend(ncol=11, loc='upper right')
# ax[0,1].set_xlim(0, time_period)
# ax[0,1].set_ylim(-20, 60)
# # ===========================================
# #                 
# # ===========================================
# ax[1,1].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['RK']), label='qd [RK]')
# ax[1,1].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['RK']), label='q [RK]')
# ax[1,1].set_ylabel('Joint angle (deg)')
# ax[1,1].legend(ncol=11, loc='upper right')
# ax[1,1].set_xlim(0, time_period)
# ax[1,1].set_ylim(-10, 90)

# # ===========================================
# #                 
# # ===========================================

# ax[2,1].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['RA']), label='qd [RA]')
# ax[2,1].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['RA']), label='q [RA]')
# ax[2,1].set_ylabel('Joint angle (deg)')
# ax[2,1].legend(ncol=11, loc='upper right')
# ax[2,1].set_xlim(0, time_period)
# ax[2,1].set_ylim(-20, 40)

# # ===========================================
# #                 
# # ===========================================

# ax[0,0].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['LH']), label='qd [LH]')
# ax[0,0].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['LH']), label='q [LH]')
# ax[0,0].set_ylabel('Joint angle (deg)')
# ax[0,0].legend(ncol=11, loc='upper right')
# ax[0,0].set_xlim(0, time_period)
# ax[0,0].set_ylim(-20, 60)

# # ===========================================
# #                 
# # ===========================================

# ax[1,0].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['LK']), label='qd [LK]')
# ax[1,0].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['LK']), label='q [LK]')
# ax[1,0].set_ylabel('Joint angle (deg)')
# ax[1,0].legend(ncol=11, loc='upper right')
# ax[1,0].set_xlim(0, time_period)
# ax[1,0].set_ylim(-10, 90)

# # ===========================================
# #                 
# # ===========================================
# ax[2,0].plot(np.array(stair_joint_cmd_df['ts']), np.array(stair_joint_cmd_df['LA']), label='qd [LA]')
# ax[2,0].plot(np.array(stair_joint_fb_df['ts']), np.array(stair_joint_fb_df['LA']), label='q [LA]')
# ax[2,0].set_ylabel('Joint angle (deg)')
# ax[2,0].legend(ncol=11, loc='upper right')
# ax[2,0].set_xlim(0, time_period)
# ax[2,0].set_ylim(-20, 40)

# # ===========================================
# #                 
# # ===========================================
# ax[3,1].plot(np.array(stair_foot_force_df['ts']), np.array(stair_foot_force_df['Rheel']), label='qd [Rheel]')
# ax[3,1].plot(np.array(stair_foot_force_df['ts']), np.array(stair_foot_force_df['Rtoe']),  label='q [Rtoe]')
# ax[3,1].set_ylabel('Joint angle (deg)')
# ax[3,1].legend(ncol=11, loc='upper right')
# ax[3,1].set_xlim(0, time_period)
# ax[3,1].set_ylim(-5, 400)

# # ===========================================
# #                 
# # ===========================================
# ax[3,0].plot(np.array(stair_foot_force_df['ts']), np.array(stair_foot_force_df['Lheel']), label='qd [Lheel]')
# ax[3,0].plot(np.array(stair_foot_force_df['ts']), np.array(stair_foot_force_df['Ltoe']), label='q [Ltoe]')
# ax[3,0].set_ylabel('Joint angle (deg)')
# ax[3,0].legend(ncol=11, loc='upper right')
# ax[3,0].set_xlim(0, time_period)
# ax[3,0].set_ylim(-5, 400)



In [6]:
# import matplotlib.pyplot as plt
# plt.rcParams['font.size'] = 13
# plt.rcParams['xtick.labelsize'] = 13 
# plt.rcParams['ytick.labelsize'] = 13 
# class ScalarFormatterClass(ScalarFormatter):
#    def _set_format(self):
#       self.format = "%1.2f"

# row_num = 4
# col_num = 2
# fig, ax = plt.subplots(row_num, col_num, sharey=False, gridspec_kw={ 'wspace':0.1, 'hspace':0.2}, figsize=(25, 10))

# time_period = 40
# # ===========================================
# #                 
# # ===========================================

# ax[0,1].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['RH']), label='qd [RH]')
# ax[0,1].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['RH']), label='q [RH]')
# ax[0,1].set_ylabel('Joint angle (deg)')
# ax[0,1].legend(ncol=11, loc='upper right')
# ax[0,1].set_xlim(0, time_period)
# ax[0,1].set_ylim(-40, 70)
# # ===========================================
# #                 
# # ===========================================
# ax[1,1].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['RK']), label='qd [RK]')
# ax[1,1].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['RK']), label='q [RK]')
# ax[1,1].set_ylabel('Joint angle (deg)')
# ax[1,1].legend(ncol=11, loc='upper right')
# ax[1,1].set_xlim(0, time_period)
# ax[1,1].set_ylim(-10, 90)

# # ===========================================
# #                 
# # ===========================================

# ax[2,1].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['RA']), label='qd [RA]')
# ax[2,1].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['RA']), label='q [RA]')
# ax[2,1].set_ylabel('Joint angle (deg)')
# ax[2,1].legend(ncol=11, loc='upper right')
# ax[2,1].set_xlim(0, time_period)
# ax[2,1].set_ylim(-20, 40)

# # ===========================================
# #                 
# # ===========================================

# ax[0,0].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['LH']), label='qd [LH]')
# ax[0,0].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['LH']), label='q [LH]')
# ax[0,0].set_ylabel('Joint angle (deg)')
# ax[0,0].legend(ncol=11, loc='upper right')
# ax[0,0].set_xlim(0, time_period)
# ax[0,0].set_ylim(-40, 70)

# # ===========================================
# #                 
# # ===========================================

# ax[1,0].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['LK']), label='qd [LK]')
# ax[1,0].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['LK']), label='q [LK]')
# ax[1,0].set_ylabel('Joint angle (deg)')
# ax[1,0].legend(ncol=11, loc='upper right')
# ax[1,0].set_xlim(0, time_period)
# ax[1,0].set_ylim(-10, 90)

# # ===========================================
# #                 
# # ===========================================
# ax[2,0].plot(np.array(sym_joint_cmd_df['ts']), np.array(sym_joint_cmd_df['LA']), label='qd [LA]')
# ax[2,0].plot(np.array(sym_joint_fb_df['ts']), np.array(sym_joint_fb_df['LA']), label='q [LA]')
# ax[2,0].set_ylabel('Joint angle (deg)')
# ax[2,0].legend(ncol=11, loc='upper right')
# ax[2,0].set_xlim(0, time_period)
# ax[2,0].set_ylim(-20, 40)

# # ===========================================
# #                 
# # ===========================================
# ax[3,1].plot(np.array(sym_foot_force_df['ts']), np.array(sym_foot_force_df['Rheel']), label='qd [Rheel]')
# ax[3,1].plot(np.array(sym_foot_force_df['ts']), np.array(sym_foot_force_df['Rtoe']),  label='q [Rtoe]')
# ax[3,1].set_ylabel('Joint angle (deg)')
# ax[3,1].legend(ncol=11, loc='upper right')
# ax[3,1].set_xlim(0, time_period)
# ax[3,1].set_ylim(-5, 400)

# # ===========================================
# #                 
# # ===========================================
# ax[3,0].plot(np.array(sym_foot_force_df['ts']), np.array(sym_foot_force_df['Lheel']), label='qd [Lheel]')
# ax[3,0].plot(np.array(sym_foot_force_df['ts']), np.array(sym_foot_force_df['Ltoe']), label='q [Ltoe]')
# ax[3,0].set_ylabel('Joint angle (deg)')
# ax[3,0].legend(ncol=11, loc='upper right')
# ax[3,0].set_xlim(0, time_period)
# ax[3,0].set_ylim(-5, 400)



## Gait cycle cut

In [7]:
from gait_cycle_cut.gait_cycle_cut import GaitCycleDetector
gait_cycle_detector = GaitCycleDetector()

for joint_angle, foot_force_heel, foot_force_toe in zip(sym_joint_fb_df['RH'], sym_foot_force_df['Rheel'], sym_foot_force_df['Rtoe']):
    gait_cycle_detector.process_step(joint_angle, foot_force_heel, foot_force_toe)


print('number of gait cycle:', gait_cycle_detector.get_number_gait_cycles())

number of gait cycle: 10


In [8]:
fig = go.Figure()
fig = make_subplots(rows=2, cols=1, shared_xaxes=False)

gait_cycles = gait_cycle_detector.get_gait_cycles()
latest_gait_cycles = gait_cycle_detector.get_latest_gait_cycle()

for i in range(len(gait_cycle_detector.get_gait_cycles())):
    fig.add_trace(go.Scatter( y=gait_cycles[i], mode='lines', name=f'gait cycle {i+1}'), row=1, col=1)

fig.add_trace(go.Scatter( y=latest_gait_cycles, mode='lines', name=f'latest gait cycle', line=dict(color='blue')), row=2, col=1)


fig.update_layout(height=600, width=1300, title="Gait cycles")
fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins
fig.show()

## DMPs learn path

In [9]:
from dmps.pydmps.dmp_discrete import DMPs_discrete
from dmps.pydmps.dmp_rhythmic import DMPs_rhythmic

In [10]:
path1 = np.array(latest_gait_cycles)
# path2 = np.array(stair_joint_fb_df['RK'])


dmp = DMPs_discrete(n_dmps=1, n_bfs=200)
dmp.imitate_path(y_des=np.array([path1]))
y_track, dy_track, ddy_track = dmp.rollout(tau=0.026) # 0.026

x_track = dmp.cs.rollout()
psi_values = dmp.gen_psi(x_track)



weighted_kernels = psi_values @ dmp.w.T


# dmp = DMPs_rhythmic(n_dmps=2, n_bfs=10000)
# dmp.imitate_path(y_des=np.array([path1, path2]))
# y_track, dy_track, ddy_track = dmp.rollout(tau=0.015)

In [11]:
fig = go.Figure()
fig = make_subplots(rows=2, cols=1, shared_xaxes=False)

fig.add_trace(go.Scatter( y=path1[:], mode='lines', name='Hip traj. [based line]', line=dict(color='red', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter( y=y_track[:, 0], mode='lines', name='Hip traj. [DMP]', line=dict(color='red' )), row=1, col=1)

fig.add_trace(go.Scatter( y=y_track[:, 0], mode='lines', name='Hip traj. [DMP]', line=dict(color='blue' )), row=2, col=1)



fig.update_layout(height=400, width=1000, title="DMP imitate Hip&Knee traj.")
fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins
fig.show()

In [12]:
fig = go.Figure()
fig = make_subplots(rows=2, cols=1, shared_xaxes=False)

for i in range(dmp.n_bfs):
    fig.add_trace(go.Scatter(x=x_track, y=psi_values[:, i], mode='lines', name=f"Basis {i+1}"), row=1, col=1)

for i in range(dmp.n_dmps):
    fig.add_trace(go.Scatter(x=x_track, y=weighted_kernels[:, i], mode='lines', name=f"Weighted Kernel {i+1}"), row=2, col=1)


fig.update_layout(height=500, width=1300, title="Kernals")
fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins
fig.show()

## CPG-RBF

In [13]:
from cpg_rbfn.cpg_afdc import CPG_AFDC
from cpg_rbfn.rbf import RBF 

cpg = CPG_AFDC()
rbf = RBF()

In [14]:
from scipy.interpolate import interp1d
# resample target
def resample_cycle(cycle, num_points):
    """Resamples a gait cycle to have a fixed number of points using interpolation."""
    original_indices = np.linspace(0, 1, len(cycle))  # original indices based on the length of the cycle
    new_indices = np.linspace(0, 1, num_points)  # new indices to match the desired number of points
    interpolation_function = interp1d(original_indices, cycle, kind='linear')  # interpolate the data
    return interpolation_function(new_indices)  # return the resampled cycle

### Offline Imitate Path Learning

In [15]:
# target = resample_cycle(np.array(gait_cycles[0]), 10000)     
# target_length = len(target)

# # Learning the path
# cpg_one_cycle = cpg.generate_cpg_one_cycle()
# out0_cpg_one_cycle = cpg_one_cycle['out0_cpg_one_cycle']
# out1_cpg_one_cycle = cpg_one_cycle['out1_cpg_one_cycle']

# # # Save to npz
# # np.savez("cpg_one_cycle", O0 = out0_converge, O1 = out1_converge) 

# out0_cpg_one_cycle = resample_cycle(out0_cpg_one_cycle, target_length)    
# out1_cpg_one_cycle = resample_cycle(out1_cpg_one_cycle, target_length)    


# cpg_kernel = rbf.construct_kernels_with_cpg_one_cycle(out0_cpg_one_cycle, out1_cpg_one_cycle, target_length)
# imitated_path_offline = rbf.imitate_path_by_learning(target)



In [16]:
# fig = go.Figure()
# fig = make_subplots(rows=6, cols=1, shared_xaxes=False)


# fig.add_trace(go.Scatter( y=cpg.out0[0], mode='lines', name=f'cpg O0'), row=1, col=1)
# fig.add_trace(go.Scatter( y=cpg.out1[0], mode='lines', name=f'cpg O1'), row=1, col=1)

# fig.add_trace(go.Scatter( y=out0_cpg_one_cycle, mode='lines', name=f'one cycle cpg O0'), row=2, col=1)
# fig.add_trace(go.Scatter( y=out1_cpg_one_cycle, mode='lines', name=f'one cycle cpg O1'), row=2, col=1)
# for i in range(len(cpg_kernel)):
#     fig.add_trace(go.Scatter( y=cpg_kernel[i], mode='lines', name=f'kernels{i}'), row=3, col=1)

# for i in range(0, len(rbf.M_stack), 100):  # Starting from 0, going up to len(rbf.M_stack), with a step of 100
#     fig.add_trace(go.Scatter(y=rbf.M_stack[i], mode='lines', name=f'evolution{i}'), row=4, col=1)


# fig.add_trace(go.Scatter( y=rbf.error_stack, mode='lines', name=f'error'), row=5, col=1)


# fig.add_trace(go.Scatter( y=imitated_path_offline, mode='lines', name=f'imitated target'), row=6, col=1)
# fig.add_trace(go.Scatter( y=target, mode='lines', name=f'target'), row=6, col=1)


# fig.update_layout(height=1000, width=1300, title="Gait cycles")
# fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins
# fig.show()

### Regenerate Path

In [17]:
# cpg_list = cpg.generate_cpg_finite_size(cpg_length=10000)

# target_weight = rbf.get_rbf_weight()
# imitated_path = []
# for out0, out1 in zip(cpg_list['out0'], cpg_list['out1']):
#     imitated_path.append(rbf.regenerate_target_traj(out0, out1, target_weight))

# imitated_path = np.asarray(imitated_path)

In [18]:
# fig = go.Figure()
# fig = make_subplots(rows=2, cols=1, shared_xaxes=False)


# fig.add_trace(go.Scatter( y=cpg_list['out0'], mode='lines', name=f'cpg O0'), row=1, col=1)
# fig.add_trace(go.Scatter( y=cpg_list['out1'], mode='lines', name=f'cpg O1'), row=1, col=1)

# x_shifted = np.arange(1000) + 550
# fig.add_trace(go.Scatter(y=imitated_path, mode='lines', name=f'imitated path'), row=2, col=1)
# fig.add_trace(go.Scatter(x=x_shifted, y=resample_cycle(imitated_path_offline, 1000), mode='lines', name=f'imitated_path_offline'), row=2, col=1)
# fig.add_trace(go.Scatter(x=x_shifted, y=resample_cycle(target, 1000), mode='lines', name=f'target'), row=2, col=1)

# fig.update_layout(height=500, width=1300, title="Gait cycles")
# fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins
# fig.show()

### Imitate new path over oldpath

In [19]:
target_1 = resample_cycle(np.array(gait_cycles[0]), 10000)     
target_1_length = len(target_1)

cpg_one_cycle = np.load('cpg_rbfn/cpg_one_cycle.npz')
out0_cpg_one_cycle = resample_cycle(cpg_one_cycle['O0'], target_1_length)    
out1_cpg_one_cycle = resample_cycle(cpg_one_cycle['O1'], target_1_length)     

cpg_kernel = rbf.construct_kernels_with_cpg_one_cycle(out0_cpg_one_cycle, out1_cpg_one_cycle, target_1_length)

imitated_path_offline_1     = rbf.imitate_path_by_learning(target_1)

In [20]:
target_2 = resample_cycle(np.array(gait_cycles[1]), 10000)     
target_2_length = len(target_2)
 
imitated_path_offline_2     = rbf.imitate_path_by_learning(target_2)


In [21]:
target_3 = resample_cycle(np.array(gait_cycles[8]), 10000)     
target_3_length = len(target_3)
 
imitated_path_offline_3     = rbf.imitate_path_by_learning(target_3)

imitated_evolution   = rbf.get_evolution_learning_path()
imitated_error   = rbf.get_error_while_learning()

In [22]:
fig = go.Figure()
fig = make_subplots(rows=6, cols=1, shared_xaxes=False)
fig.update_layout(height=1000, width=1300, title="Evolution plot")
fig.update_layout(margin=dict(l=10, r=10, t=40, b=10))  # Reduce margins



# for i in range(len(cpg_kernel)):
#     fig.add_trace(go.Scatter( y=cpg_kernel[i], mode='lines', name=f'kernels{i}'), row=1, col=1)

# for i in range(0, len(imitated_evolution), 100):  # Starting from 0, going up to len(rbf.M_stack), with a step of 100
#     fig.add_trace(go.Scatter(y=imitated_evolution[i], mode='lines', name=f'evolution{i}'), row=2, col=1)


for i in range(5):  
    fig.add_trace(go.Scatter(y=imitated_evolution[i], mode='lines', name=f'evolution{i}'), row=2, col=1)
for i in range(500,505):  
    fig.add_trace(go.Scatter(y=imitated_evolution[i], mode='lines', name=f'evolution{i}'), row=2, col=1)
for i in range(1000,1005):  
    fig.add_trace(go.Scatter(y=imitated_evolution[i], mode='lines', name=f'evolution{i}'), row=2, col=1)


fig.add_trace(go.Scatter( y=imitated_error, mode='lines', name=f'error'), row=3, col=1)


fig.add_trace(go.Scatter( y=imitated_path_offline_1, mode='lines', name=f'imitated target 1'), row=4, col=1)
# fig.add_trace(go.Scatter( y=target_1, mode='lines', name=f'target 1'), row=4, col=1)

fig.add_trace(go.Scatter( y=imitated_path_offline_2, mode='lines', name=f'imitated target 2'), row=4, col=1)
# fig.add_trace(go.Scatter( y=target_2, mode='lines', name=f'target 2'), row=4, col=1)

fig.add_trace(go.Scatter( y=imitated_path_offline_3, mode='lines', name=f'imitated target 3'), row=4, col=1)
# fig.add_trace(go.Scatter( y=target_3, mode='lines', name=f'target 3'), row=4, col=1)

fig.show()

In [23]:
# gait_cycles[0] cannot completely learn